In [ ]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

In [ ]:
def knapsack_recursive(items, C):
    """
    items: a list of (weight, value) pairs
    C: the maximum total weight
    
    Returns (best value, list of items in a solution)
    """
    if len(items) == 0:
        return (0, [])
    w, v = items[0]
    soln_without = knapsack_recursive(items[1:], C)
    if w > C:
        return soln_without
    else:
        value, choices = knapsack_recursive(items[1:], C - w)
        soln_with = (value + v, [(w, v)] + choices)
        return max(soln_with, soln_without)    

In [ ]:
# Check on some examples.

items = [(3,4)]
print(knapsack_recursive(items, 2))
items = [(3,4), (5,4), (6,5), (9,7)]
print(knapsack_recursive(items, 9))
items = [(3,4), (5,4), (6,5), (9,7), (1,2)]
print(knapsack_recursive(items, 9))


In [ ]:
#How does this scale? let's try random instances:
import random

def make_instance(n, maxW, maxV):
    items = [(random.randint(1, maxW), random.randint(1, maxV)) for _ in range(n)]
    # Capacity such that we will take Theta(n) items
    C = n*maxW // 2
    return (items, C)

for n in [1, 10, 15, 20, 21]:
    print(f"n = {n}:")
    %timeit knapsack_recursive(*make_instance(n, 1000,1000))

In [ ]:
# Let's try the same `memoize` as pset 1
# (slightly modified to work with mutable inputs)
import functools
import pickle

def memoize(f):
    """This can turn any recursive function into a memoized version."""
    cache = {}
    @functools.wraps(f)
    def wrap(*args):
        args_hash = pickle.dumps(args)
        if args_hash not in cache:
            cache[args_hash] = f(*args)  
        return cache[args_hash]
    wrap.cache = cache                #so we can clear it as needed
    return wrap

In [ ]:
knapsack_original_recursive = knapsack_recursive
knapsack_recursive = memoize(knapsack_recursive)

%timeit -n 1 knapsack_recursive(*make_instance(21, 1000,1000))

In [ ]:
# OK, there's an issue with using @memoize for timing, which is that the cache is shared
# across multiple calls.  This creates a new function, knapsack_memoized, that clears
# the cache.

@functools.wraps(knapsack_recursive)
def knapsack_memoized(*args):
    knapsack_recursive.cache = {}
    return knapsack_recursive(*args)

In [ ]:
items = [(3,4), (5,4), (6,5), (9,7), (1,2)]
print(knapsack_memoized(items, 9))
for n in [1, 10, 15, 20, 21, 50]:
    print(f"n = {n}:")
    %timeit knapsack_memoized(*make_instance(n, 1000,1000))

Question (a):
------------

What are the big-O time and space complexity of `knapsack_memoized`?  Give your answer both as a function of `n` and `C`, and as a function of `n` for an instance of `make_instance(n, 1000, 1000)`.

In [ ]:
# Now let's try the bottom-up DP, with a sliding window.

def knapsack_value(items, C):
    best = [0]*(C+1)
    for w, v in items:
        # By iterating t from the end to the beginning, we can keep only one column
        for t in range(C, w-1, -1):
            best[t] = max(best[t], best[t-w]+v)
    return best[C]

In [ ]:
items = [(3,4), (5,4), (6,5), (9,7), (1,2)]
print(knapsack_value(items, 9))
for n in [1, 10, 15, 20, 21, 50]:
    print(f"n = {n}:")
    %timeit knapsack_value(*make_instance(n, 1000,1000))

In [ ]:
# Python loops are slow.  Let's make it faster by making the inner loop an array operation,
# which numpy can do 50-100 times faster than python loops.

def knapsack_value_numpy(items, C):
    best = np.zeros(C+1)
    for w, v in items:
        best[w:] = np.max([best[w:], best[:-w] + v], axis=0)
    return best[C]

In [ ]:
items = [(3,4), (5,4), (6,5), (9,7), (1,2)]
print(knapsack_value_numpy(items, 9))
for n in [1, 10, 15, 20, 21, 50]:
    print(f"n = {n}:")
    %timeit knapsack_value_numpy(*make_instance(n, 1000,1000))

In [ ]:
# Timing code from fibonacci

import timeit

def smarter_timeit(f, min_total_time=0.1):
    """Figure out how long f() takes to run.
    
    To make the timing reliable, run the function enough times to take min_time seconds overall.
    """
    number = 1
    while True:
        total_time = timeit.timeit(f, number=number)
        if total_time > min_total_time:
            return total_time / number
        number *= 2
        
# Get all the data
def get_times(func, base=1.01, max_val=None, max_time=2, min_time=0.5):
    """Get the running time for a given function at many different n.
    
    Gets the time to compute func(n) for n growing up until it takes
    max_time seconds to compute func(n), and return a pair of lists:
    the times and corresponding ns. 
    """
    nums = []
    vals = []
    for i in range(1000):
        n = int(base**i)
        if nums and n == nums[-1]:
            continue
        if max_val is not None and n > max_val:
            break
        t = smarter_timeit(lambda: func(n), min_time)
        nums.append(n)
        vals.append(t)
        if t > max_time:
            break
    return nums, vals

In [ ]:
funcs = [('memoized', knapsack_memoized),
         ('bottom-up', knapsack_value),
         ('bottom-up numpy', knapsack_value_numpy),
        ]

timings = {}

for label, f in funcs:
    timings[label] = get_times(lambda n: f(*make_instance(n, 1000,1000)), 1.4)

In [ ]:
for label, times in timings.items():
    plt.plot(*times, marker='o', label=label)
plt.legend()

In [ ]:
for label, times in timings.items():
    plt.plot(*times, marker='o', label=label)
plt.legend()
plt.loglog()

Question (b):
----------------

In our input instances, both the weights and values are small integers, bounded by `B = 1000`.  What is the running time as a function of `n` and `B`?

Does the growth with `n` conform to what you see on this log-log plot?

Question (c):
--------------
Implement a version of `knapsack_value` or `knapsack_value_numpy` that also finds the set of items.

(You may use O(nC) space if you prefer, but I encourage you to implement and compare to the O(C) space algorithm.)

In [ ]:
def knapsack_set(items, C):
    ...
    return ans

Question (d)
----------------

How does the timing of your `knapsack_set` compare to `knapsack_value`, both theoretically and empirically?

Question (e)   _(optional)_ 
------------

The knapsack problem is in general NP-hard when both the weights and values are arbitrary real numbers.
However, _random instances_ like those generated by `make_instance(n, 2**30, 2**30)` are actually easy to
solve in polynomial time with high probability.

Design and implement an algorithm that can do so.  (No proof necessary, just empirical evidence)

Hint: The `best` array from knapsack_value is usually highly redundant, and the set of "Pareto-optimal" points is much smaller.

In [ ]:
def knapsack_value_high(items, C):
    ...
    return best[-1][1]

In [ ]:
random.seed(3)
print(knapsack_value_high(*make_instance(100, 2**30,2**30)))
# Should give: 48957779005

%timeit knapsack_value_high(*make_instance(100, 2**30,2**30))
# My code is 10 lines long and takes 11 ms per loop
